In [1]:
# import AWS credentials
# import config.py ##for local
%run "/dbfs/FileStore/tables/config" ##for databricks

In [2]:
import pandas as pd
import numpy as np

from pyspark.sql import SparkSession
from pyspark import SparkFiles
from pyspark.sql import DataFrame
from pyspark.sql.types import *
import pyspark.sql.functions as F

In [3]:
# get or create Spark session
app_name = "spark-airbnb-sentiment"
spark = SparkSession.builder.appName(app_name).getOrCreate()

In [4]:
import boto3

secret_name = my_secret_name
region_name = my_region_name
access_key  = my_access_key
secret_key  = my_secret_key

session      = boto3.session.Session(aws_access_key_id=access_key, aws_secret_access_key=secret_key, region_name=region_name)
client       = session.client('secretsmanager')
secret_value = client.get_secret_value(SecretId=secret_name)

In [5]:
import json
def get_connection(secret_value):
    return json.loads(secret_value['SecretString'])

In [6]:
connection = get_connection(secret_value)

# Postgres credentials
jdbcHostname = connection['host']
jdbcPort     = connection['port']
jdbcDatabase = "postgres"
dialect      = "postgresql"
jdbcUsername = connection['username']
jdbcPassword = connection['password']

jdbcUrl = f"jdbc:{dialect}://{jdbcHostname}:{jdbcPort}/{jdbcDatabase}"
connectionProperties = {
  "user"     : jdbcUsername,
  "password" : jdbcPassword,
  "driver"   : "org.postgresql.Driver" 
}

In [7]:
# Read from reviews_full table

table = "reviews_full"

reviews_df = spark.read.jdbc(url=jdbcUrl, table=table, properties=connectionProperties)
reviews_df.printSchema()

root
-- listing_id: integer (nullable = true)
-- id: integer (nullable = true)
-- date: date (nullable = true)
-- reviewer_id: integer (nullable = true)
-- reviewer_name: string (nullable = true)
-- comments: string (nullable = true)

In [8]:
from pyspark.ml import Pipeline
import sparknlp
sparknlp.start()
from sparknlp.base import *
from sparknlp.annotator import *
from sparknlp.pretrained import PretrainedPipeline

pipeline = PretrainedPipeline("explain_document_ml", lang="en")

explain_document_ml download started this may take some time.
Approx size to download 9.4 MB
[ | ][ / ][ — ][ \ ][ | ][ / ][ — ][ \ ][ | ][ / ][ — ][OK!]

In [9]:
reviews_df = reviews_df.withColumnRenamed("comments", "text").filter("text IS NOT NULL")

In [10]:
annotations_df = pipeline.transform(reviews_df)

In [11]:
display(annotations_df)

listing_id id date reviewer_id reviewer_name text document sentence token checked lemma stem pos 5456 16489 2009-11-07 46119 Kevin Very accommodating, great space. List(List(document, 0, 31, Very accommodating, great space., Map(sentence -> 0), List())) List(List(document, 0, 31, Very accommodating, great space., Map(sentence -> 0), List())) List(List(token, 0, 3, Very, Map(sentence -> 0), List()), List(token, 5, 17, accommodating, Map(sentence -> 0), List()), List(token, 18, 18, ,, Map(sentence -> 0), List()), List(token, 20, 24, great, Map(sentence -> 0), List()), List(token, 26, 30, space, Map(sentence -> 0), List()), List(token, 31, 31, ., Map(sentence -> 0), List())) List(List(token, 0, 3, Very, Map(confidence -> 1.0), List()), List(token, 5, 17, accommodating, Map(confidence -> 1.0), List()), List(token, 18, 18, ,, Map(confidence -> 0.0), List()), List(token, 20, 24, great, Map(confidence -> 1.0), List()), List(token, 26, 30, space, Map(confidence -> 1.0), List()), List(token, 31, 31, ., Map(confidence -> 0.0), List())) List(List(token, 0, 3, Very, Map(confidence -> 1.0), List()), List(token, 5, 17, accommodate, Map(confidence -> 1.0), List()), List(token, 18, 18, ,, Map(confidence -> 0.0), List()), List(token, 20, 24, great, Map(confidence -> 1.0), List()), List(token, 26, 30, space, Map(confidence -> 1.0), List()), List(token, 31, 31, ., Map(confidence -> 0.0), List())) List(List(token, 0, 3, veri, Map(confidence -> 1.0), List()), List(token, 5, 17, accommod, Map(confidence -> 1.0), List()), List(token, 18, 18, ,, Map(confidence -> 0.0), List()), List(token, 20, 24, great, Map(confidence -> 1.0), List()), List(token, 26, 30, space, Map(confidence -> 1.0), List()), List(token, 31, 31, ., Map(confidence -> 0.0), List())) List(List(pos, 0, 3, RB, Map(word -> Very), List()), List(pos, 5, 17, VBG, Map(word -> accommodating), List()), List(pos, 18, 18, ,, Map(word -> ,), List()), List(pos, 20, 24, JJ, Map(word -> great), List()), List(pos, 26, 30, NN, Map(word -> space), List()), List(pos, 31, 31, ., Map(word -> .), List())) 5456 18215 2009-11-24 54243 Jane 6th Street is a bit of a walk but location is central to lots of shopping, nightlife and eateries. Place is clean, private and offers an array of videos and dcs. Great coffee, coffee pot and Fiesta Ware in the kitchen. List(List(document, 0, 217, 6th Street is a bit of a walk but location is central to lots of shopping, nightlife and eateries. Place is clean, private and offers an array of videos and dcs. Great coffee, coffee pot and Fiesta Ware in the kitchen., Map(sentence -> 0), List())) List(List(document, 0, 97, 6th Street is a bit of a walk but location is central to lots of shopping, nightlife and eateries., Map(sentence -> 0), List()), List(document, 99, 160, Place is clean, private and offers an array of videos and dcs., Map(sentence -> 1), List()), List(document, 162, 217, Great coffee, coffee pot and Fiesta Ware in the kitchen., Map(sentence -> 2), List())) List(List(token, 0, 2, 6th, Map(sentence -> 0), List()), List(token, 4, 9, Street, Map(sentence -> 0), List()), List(token, 11, 12, is, Map(sentence -> 0), List()), List(token, 14, 14, a, Map(sentence -> 0), List()), List(token, 16, 18, bit, Map(sentence -> 0), List()), List(token, 20, 21, of, Map(sentence -> 0), List()), List(token, 23, 23, a, Map(sentence -> 0), List()), List(token, 25, 28, walk, Map(sentence -> 0), List()), List(token, 30, 32, but, Map(sentence -> 0), List()), List(token, 34, 41, location, Map(sentence -> 0), List()), List(token, 43, 44, is, Map(sentence -> 0), List()), List(token, 46, 52, central, Map(sentence -> 0), List()), List(token, 54, 55, to, Map(sentence -> 0), List()), List(token, 57, 60, lots, Map(sentence -> 0), List()), List(token, 62, 63, of, Map(sentence -> 0), List()), List(token, 65, 72, shopping, Map(sentence -> 0), List()), List(token, 73, 73, ,, Map(sentence -> 0), List()), List(token, 75, 83, nightlife, Map(sentence -> 0), List()), List(token, 85, 87, and, Map(sentenc

In [12]:
stop_words_cleaner = StopWordsCleaner() \
        .setInputCols(["token"]) \
        .setOutputCol("cleanTokens") \
        .setCaseSensitive(False) \
        .setStopWords(["this", "is", "and", ",", "!", ".", "\n", "\t", "ourselves", "hers", "between", "yourself", "but", "again", "there", "about", "once", "during", "out", "very", "having", "with", "they", "own", "an", "be", "some", "for", "do", "its", "yours", "such", "into", "of", "most", "itself", "other", "off", "is", "s", "am", "or", "who", "as", "from", "him", "each", "the", "themselves", "until", "below", "are", "we", "these", "your", "his", "through", "don", "nor", "me", "were", "her", "more", "himself", "this", "down", "should", "our", "their", "while", "above", "both", "up", "to", "ours", "had", "she", "all", "no", "when", "at", "any", "before", "them", "same", "and", "been", "have", "in", "will", "on", "does", "yourselves", "then", "that", "because", "what", "over", "why", "so", "can", "did", "not", "now", "under", "he", "you", "herself", "has", "just", "where", "too", "only", "myself", "which", "those", "i", "after", "few", "whom", "t", "being", "if", "theirs", "my", "against", "a", "by", "doing", "it", "how", "further", "was", "here", "than", "(", ")", "-", "/", ";"])

unigrams = NGramGenerator() \
            .setInputCols(["cleanTokens"]) \
            .setOutputCol("unigrams") \
            .setN(1) \
            .setEnableCumulative(False)

bigrams = NGramGenerator() \
            .setInputCols(["cleanTokens"]) \
            .setOutputCol("bigrams") \
            .setN(2) \
            .setEnableCumulative(False)

extra_pipeline = Pipeline(
    stages = [
      stop_words_cleaner,
      unigrams,
      bigrams
  ])

In [13]:
model = extra_pipeline.fit(annotations_df)
annotations_df = model.transform(annotations_df)

In [14]:
display(annotations_df)

listing_id id date reviewer_id reviewer_name text document sentence token checked lemma stem pos cleanTokens unigrams bigrams 5456 16489 2009-11-07 46119 Kevin Very accommodating, great space. List(List(document, 0, 31, Very accommodating, great space., Map(sentence -> 0), List())) List(List(document, 0, 31, Very accommodating, great space., Map(sentence -> 0), List())) List(List(token, 0, 3, Very, Map(sentence -> 0), List()), List(token, 5, 17, accommodating, Map(sentence -> 0), List()), List(token, 18, 18, ,, Map(sentence -> 0), List()), List(token, 20, 24, great, Map(sentence -> 0), List()), List(token, 26, 30, space, Map(sentence -> 0), List()), List(token, 31, 31, ., Map(sentence -> 0), List())) List(List(token, 0, 3, Very, Map(confidence -> 1.0), List()), List(token, 5, 17, accommodating, Map(confidence -> 1.0), List()), List(token, 18, 18, ,, Map(confidence -> 0.0), List()), List(token, 20, 24, great, Map(confidence -> 1.0), List()), List(token, 26, 30, space, Map(confidence -> 1.0), List()), List(token, 31, 31, ., Map(confidence -> 0.0), List())) List(List(token, 0, 3, Very, Map(confidence -> 1.0), List()), List(token, 5, 17, accommodate, Map(confidence -> 1.0), List()), List(token, 18, 18, ,, Map(confidence -> 0.0), List()), List(token, 20, 24, great, Map(confidence -> 1.0), List()), List(token, 26, 30, space, Map(confidence -> 1.0), List()), List(token, 31, 31, ., Map(confidence -> 0.0), List())) List(List(token, 0, 3, veri, Map(confidence -> 1.0), List()), List(token, 5, 17, accommod, Map(confidence -> 1.0), List()), List(token, 18, 18, ,, Map(confidence -> 0.0), List()), List(token, 20, 24, great, Map(confidence -> 1.0), List()), List(token, 26, 30, space, Map(confidence -> 1.0), List()), List(token, 31, 31, ., Map(confidence -> 0.0), List())) List(List(pos, 0, 3, RB, Map(word -> Very), List()), List(pos, 5, 17, VBG, Map(word -> accommodating), List()), List(pos, 18, 18, ,, Map(word -> ,), List()), List(pos, 20, 24, JJ, Map(word -> great), List()), List(pos, 26, 30, NN, Map(word -> space), List()), List(pos, 31, 31, ., Map(word -> .), List())) List(List(token, 5, 17, accommodating, Map(sentence -> 0), List()), List(token, 20, 24, great, Map(sentence -> 0), List()), List(token, 26, 30, space, Map(sentence -> 0), List())) List(List(chunk, 5, 17, accommodating, Map(sentence -> 0), List()), List(chunk, 20, 24, great, Map(sentence -> 0), List()), List(chunk, 26, 30, space, Map(sentence -> 0), List())) List(List(chunk, 5, 24, accommodating great, Map(sentence -> 0), List()), List(chunk, 20, 30, great space, Map(sentence -> 0), List())) 5456 18215 2009-11-24 54243 Jane 6th Street is a bit of a walk but location is central to lots of shopping, nightlife and eateries. Place is clean, private and offers an array of videos and dcs. Great coffee, coffee pot and Fiesta Ware in the kitchen. List(List(document, 0, 217, 6th Street is a bit of a walk but location is central to lots of shopping, nightlife and eateries. Place is clean, private and offers an array of videos and dcs. Great coffee, coffee pot and Fiesta Ware in the kitchen., Map(sentence -> 0), List())) List(List(document, 0, 97, 6th Street is a bit of a walk but location is central to lots of shopping, nightlife and eateries., Map(sentence -> 0), List()), List(document, 99, 160, Place is clean, private and offers an array of videos and dcs., Map(sentence -> 1), List()), List(document, 162, 217, Great coffee, coffee pot and Fiesta Ware in the kitchen., Map(sentence -> 2), List())) List(List(token, 0, 2, 6th, Map(sentence -> 0), List()), List(token, 4, 9, Street, Map(sentence -> 0), List()), List(token, 11, 12, is, Map(sentence -> 0), List()), List(token, 14, 14, a, Map(sentence -> 0), List()), List(token, 16, 18, bit, Map(sentence -> 0), List()), List(token, 20, 21, of, Map(sentence -> 0), List()), List(token, 23, 23, a, Map(sentence -> 0), List()), List(token, 25, 28, walk, Map(sentence -> 0), List()), List(token, 30, 32, but, Map(sentence -> 0), List()), List(token, 3

In [15]:
listings_df = spark.read.jdbc(url=jdbcUrl, table="listings_full", properties=connectionProperties)
listings_df = listings_df.select("id", "neighbourhood_cleansed")

In [16]:
labeled_df = annotations_df.withColumnRenamed("id", "review_id")\
                           .join(listings_df, annotations_df.listing_id == listings_df.id, how="inner") \
                           .drop(F.col("id"))

In [17]:
display(labeled_df)

listing_id review_id date reviewer_id reviewer_name text document sentence token checked lemma stem pos cleanTokens unigrams bigrams neighbourhood_cleansed 32396 69154 2010-07-25 177802 Mariana We had a great time. The location was perfect for us, only a few mins from downtown and yet in a nice friendly neighborhood. Parking was avaiable.
The house was clean and organized. The room and private bathroom were well equipped with all we needed.

Tiffany was very hospitable. She invited us to eat or drink anything she had in the fridge and sent us an email before arrival with all the information we needed to enjoy the house to the fullest.

I would definitely recommend "South Austin Confort" to anyone! and we are already making plans to possibly go back next summer! List(List(document, 0, 584, We had a great time. The location was perfect for us, only a few mins from downtown and yet in a nice friendly neighborhood. Parking was avaiable.
The house was clean and organized. The room and private bathroom were well equipped with all we needed.

Tiffany was very hospitable. She invited us to eat or drink anything she had in the fridge and sent us an email before arrival with all the information we needed to enjoy the house to the fullest.

I would definitely recommend "South Austin Confort" to anyone! and we are already making plans to possibly go back next summer!, Map(sentence -> 0), List())) List(List(document, 0, 19, We had a great time., Map(sentence -> 0), List()), List(document, 22, 124, The location was perfect for us, only a few mins from downtown and yet in a nice friendly neighborhood., Map(sentence -> 1), List()), List(document, 126, 146, Parking was avaiable., Map(sentence -> 2), List()), List(document, 149, 182, The house was clean and organized., Map(sentence -> 3), List()), List(document, 185, 252, The room and private bathroom were well equipped with all we needed., Map(sentence -> 4), List()), List(document, 257, 284, Tiffany was very hospitable., Map(sentence -> 5), List()), List(document, 287, 453, She invited us to eat or drink anything she had in the fridge and sent us an email before arrival with all the information we needed to enjoy the house to the fullest., Map(sentence -> 6), List()), List(document, 458, 519, I would definitely recommend "South Austin Confort" to anyone!, Map(sentence -> 7), List()), List(document, 521, 584, and we are already making plans to possibly go back next summer!, Map(sentence -> 8), List())) List(List(token, 0, 1, We, Map(sentence -> 0), List()), List(token, 3, 5, had, Map(sentence -> 0), List()), List(token, 7, 7, a, Map(sentence -> 0), List()), List(token, 9, 13, great, Map(sentence -> 0), List()), List(token, 15, 18, time, Map(sentence -> 0), List()), List(token, 19, 19, ., Map(sentence -> 0), List()), List(token, 22, 24, The, Map(sentence -> 1), List()), List(token, 26, 33, location, Map(sentence -> 1), List()), List(token, 35, 37, was, Map(sentence -> 1), List()), List(token, 39, 45, perfect, Map(sentence -> 1), List()), List(token, 47, 49, for, Map(sentence -> 1), List()), List(token, 51, 52, us, Map(sentence -> 1), List()), List(token, 53, 53, ,, Map(sentence -> 1), List()), List(token, 55, 58, only, Map(sentence -> 1), List()), List(token, 60, 60, a, Map(sentence -> 1), List()), List(token, 62, 64, few, Map(sentence -> 1), List()), List(token, 66, 69, mins, Map(sentence -> 1), List()), List(token, 71, 74, from, Map(sentence -> 1), List()), List(token, 76, 83, downtown, Map(sentence -> 1), List()), List(token, 85, 87, and, Map(sentence -> 1), List()), List(token, 89, 91, yet, Map(sentence -> 1), List()), List(token, 93, 94, in, Map(sentence -> 1), List()), List(token, 96, 96, a, Map(sentence -> 1), List()), List(token, 98, 101, nice, Map(sentence -> 1), List()), List(token, 103, 110, friendly, Map(sentence -> 1), List()), List(token, 112, 123, neighborhood, Map(sentence -> 1), List()), List(token, 124, 124, ., Map(sentence -> 1), List()), List(token, 126, 132, Parki

In [18]:
# extract ngram results into list
@F.udf()
def extract_results(ngram):
  combined_result = [x["result"] for x in ngram ]
  return combined_result

In [19]:
output_df = labeled_df.select("listing_id", "neighbourhood_cleansed", \
                                             extract_results("unigrams").alias("unigram_list"), \
                                             extract_results("bigrams").alias("bigram_list")
                             ).withColumnRenamed("neighbourhood_cleansed", "zipcode")

In [20]:
display(output_df)

listing_id zipcode unigram_list bigram_list 32396 78749 [great, time, location, perfect, us, mins, downtown, yet, nice, friendly, neighborhood, Parking, avaiable, house, clean, organized, room, private, bathroom, well, equipped, needed, Tiffany, hospitable, invited, us, eat, drink, anything, fridge, sent, us, email, arrival, information, needed, enjoy, house, fullest, would, definitely, recommend, ", South, Austin, Confort, ", anyone, already, making, plans, possibly, go, back, next, summer] [great time, location perfect, perfect us, us mins, mins downtown, downtown yet, yet nice, nice friendly, friendly neighborhood, Parking avaiable, house clean, clean organized, room private, private bathroom, bathroom well, well equipped, equipped needed, Tiffany hospitable, invited us, us eat, eat drink, drink anything, anything fridge, fridge sent, sent us, us email, email arrival, arrival information, information needed, needed enjoy, enjoy house, house fullest, would definitely, definitely recommend, recommend ", " South, South Austin, Austin Confort, Confort ", " anyone, already making, making plans, plans possibly, possibly go, go back, back next, next summer] 32396 78749 [time, life, Austin, thanks, Tiff, educated, Austin, landmarks, well, great, places, dine, Plus, house, immaculate, plan, going, back, next, year] [time life, life Austin, Austin thanks, thanks Tiff, educated Austin, Austin landmarks, landmarks well, well great, great places, places dine, Plus house, house immaculate, plan going, going back, back next, next year] 32396 78749 [girlfriend, amazing, time, Austin, Tiff's, house, really, really, clean, provided, everything, needed, coolest, thing, educated, area, lot, offer, us, would, definitely, stay, already, recommending, airbnb, friends, family, great, experience, Tiff, Thanks, Tiff] [girlfriend amazing, amazing time, time Austin, Tiff's house, house really, really really, really clean, clean provided, provided everything, everything needed, coolest thing, thing educated, educated area, area lot, lot offer, offer us, would definitely, definitely stay, stay already, already recommending, recommending airbnb, airbnb friends, friends family, family great, great experience, experience Tiff, Thanks Tiff] 32396 78749 [girlfriend, amazing, time, Tiffany's, apartment, place, large, clean, every, amenity, need, parking, backyard, kitchen, TV, etc, Tiffany, outstanding, host, absolutely, reason, stay, anywhere, else, Austin, Everything, location, pet, dogs, perfect] [girlfriend amazing, amazing time, time Tiffany's, Tiffany's apartment, place large, large clean, clean every, every amenity, amenity need, need parking, parking backyard, backyard kitchen, kitchen TV, TV etc, Tiffany outstanding, outstanding host, host absolutely, absolutely reason, reason stay, stay anywhere, anywhere else, else Austin, Everything location, location pet, pet dogs, dogs perfect] 32396 78749 [really, enjoyed, stay, w/TK, friendly, house, comfortable, clean, would, stay, positive, experience] [really enjoyed, enjoyed stay, stay w/TK, friendly house, house comfortable, comfortable clean, would stay, positive experience] 32396 78749 [stayed, TK's, house, SXSW, festival, 2011, edition, great, little, quiet, place, rest, noise, town, house, clean, well, equiped, charming, nice, neighborhood, recommand, renting, car, Parking, downtown, easy, expansive, Lots, parking, space, 10$, per, day, Easier, relying, taxi, difficult, get, night, would, like, add, TK, nicest, person, provided, us, plenty, useful, information, get, around] [stayed TK's, TK's house, house SXSW, SXSW festival, festival 2011, 2011 edition, edition great, little quiet, quiet place, place rest, rest noise, noise town, house clean, clean well, well equiped, equiped charming, charming nice, nice neighborhood, recommand renting, renting car, Parking downtown, downtown easy, easy expansive, Lots parking, parking space, space 10$, 10$ per, per day, Easier relying, relying taxi, difficult get, 

In [21]:
test_df = output_df.limit(2)

In [22]:
test_df.show()

+----------+-------+--------------------+--------------------+
listing_id|zipcode| unigram_list| bigram_list|
+----------+-------+--------------------+--------------------+
 32396| 78749|[great, time, loc...|[great time, loca...|
 32396| 78749|[time, life, Aust...|[time life, life ...|
+----------+-------+--------------------+--------------------+

In [23]:
display(test_df.groupBy("zipcode").agg(F.collect_list('unigram_list').alias("unigram_list"), F.collect_list('bigram_list').alias("bigram_list")))

zipcode unigram_list bigram_list 78749 List([great, time, location, perfect, us, mins, downtown, yet, nice, friendly, neighborhood, Parking, avaiable, house, clean, organized, room, private, bathroom, well, equipped, needed, Tiffany, hospitable, invited, us, eat, drink, anything, fridge, sent, us, email, arrival, information, needed, enjoy, house, fullest, would, definitely, recommend, ", South, Austin, Confort, ", anyone, already, making, plans, possibly, go, back, next, summer], [time, life, Austin, thanks, Tiff, educated, Austin, landmarks, well, great, places, dine, Plus, house, immaculate, plan, going, back, next, year]) List([great time, location perfect, perfect us, us mins, mins downtown, downtown yet, yet nice, nice friendly, friendly neighborhood, Parking avaiable, house clean, clean organized, room private, private bathroom, bathroom well, well equipped, equipped needed, Tiffany hospitable, invited us, us eat, eat drink, drink anything, anything fridge, fridge sent, sent us, us email, email arrival, arrival information, information needed, needed enjoy, enjoy house, house fullest, would definitely, definitely recommend, recommend ", " South, South Austin, Austin Confort, Confort ", " anyone, already making, making plans, plans possibly, possibly go, go back, back next, next summer], [time life, life Austin, Austin thanks, thanks Tiff, educated Austin, Austin landmarks, landmarks well, well great, great places, places dine, Plus house, house immaculate, plan going, going back, back next, next year])

In [24]:
agg_output_df = output_df.groupBy("zipcode").agg(F.collect_list('unigram_list').alias("unigram_list"), F.collect_list('bigram_list').alias("bigram_list"))

In [25]:
display(agg_output_df)

org.apache.spark.sql.AnalysisException: CSV data source does not support array data type.;
	at org.apache.spark.sql.execution.datasources.DataSourceUtils$$anonfun$verifySchema$1.apply(DataSourceUtils.scala:69)
	at org.apache.spark.sql.execution.datasources.DataSourceUtils$$anonfun$verifySchema$1.apply(DataSourceUtils.scala:67)
	at scala.collection.Iterator$class.foreach(Iterator.scala:891)
	at scala.collection.AbstractIterator.foreach(Iterator.scala:1334)
	at scala.collection.IterableLike$class.foreach(IterableLike.scala:72)
	at org.apache.spark.sql.types.StructType.foreach(StructType.scala:99)
	at org.apache.spark.sql.execution.datasources.DataSourceUtils$.verifySchema(DataSourceUtils.scala:67)
	at org.apache.spark.sql.execution.datasources.DataSourceUtils$.verifyWriteSchema(DataSourceUtils.scala:34)
	at org.apache.spark.sql.execution.datasources.FileFormatWriter$.write(FileFormatWriter.scala:104)
	at org.apache.spark.sql.execution.datasources.InsertIntoHadoopFsRelationCommand.run(InsertIntoHadoopFsRelationCommand.scala:192)
	at org.apache.spark.sql.execution.command.DataWritingCommandExec.sideEffectResult$lzycompute(commands.scala:108)
	at org.apache.spark.sql.execution.command.DataWritingCommandExec.sideEffectResult(commands.scala:106)
	at org.apache.spark.sql.execution.command.DataWritingCommandExec.doExecute(commands.scala:126)
	at org.apache.spark.sql.execution.SparkPlan$$anonfun$execute$1.apply(SparkPlan.scala:146)
	at org.apache.spark.sql.execution.SparkPlan$$anonfun$execute$1.apply(SparkPlan.scala:134)
	at org.apache.spark.sql.execution.SparkPlan$$anonfun$executeQuery$5.apply(SparkPlan.scala:187)
	at org.apache.spark.rdd.RDDOperationScope$.withScope(RDDOperationScope.scala:151)
	at org.apache.spark.sql.execution.SparkPlan.executeQuery(SparkPlan.scala:183)
	at org.apache.spark.sql.execution.SparkPlan.execute(SparkPlan.scala:134)
	at org.apache.spark.sql.execution.QueryExecution.toRdd$lzycompute(QueryExecution.scala:115)
	at org.apache.spark.sql.execution.QueryExecution.toRdd(QueryExecution.scala:115)
	at org.apache.spark.sql.DataFrameWriter$$anonfun$runCommand$1.apply(DataFrameWriter.scala:710)
	at org.apache.spark.sql.DataFrameWriter$$anonfun$runCommand$1.apply(DataFrameWriter.scala:710)
	at org.apache.spark.sql.execution.SQLExecution$$anonfun$withCustomExecutionEnv$1.apply(SQLExecution.scala:111)
	at org.apache.spark.sql.execution.SQLExecution$.withSQLConfPropagated(SQLExecution.scala:240)
	at org.apache.spark.sql.execution.SQLExecution$.withCustomExecutionEnv(SQLExecution.scala:97)
	at org.apache.spark.sql.execution.SQLExecution$.withNewExecutionId(SQLExecution.scala:170)
	at org.apache.spark.sql.DataFrameWriter.runCommand(DataFrameWriter.scala:710)
	at org.apache.spark.sql.DataFrameWriter.saveToV1Source(DataFrameWriter.scala:306)
	at org.apache.spark.sql.DataFrameWriter.save(DataFrameWriter.scala:292)
	at com.databricks.SparkShim$.saveAsCSV(SparkShim.scala:53)
	at com.databricks.backend.daemon.driver.OutputAggregator$$anonfun$com$databricks$backend$daemon$driver$OutputAggregator$$storeResultsToDBFS$1.apply$mcV$sp(OutputAggregator.scala:188)
	at com.databricks.backend.daemon.driver.OutputAggregator$$anonfun$com$databricks$backend$daemon$driver$OutputAggregator$$storeResultsToDBFS$1.apply(OutputAggregator.scala:188)
	at com.databricks.backend.daemon.driver.OutputAggregator$$anonfun$com$databricks$backend$daemon$driver$OutputAggregator$$storeResultsToDBFS$1.apply(OutputAggregator.scala:188)
	at com.databricks.sql.acl.CheckPermissions$.trusted(CheckPermissions.scala:812)
	at com.databricks.backend.daemon.driver.OutputAggregator$.com$databricks$backend$daemon$driver$OutputAggregator$$storeResultsToDBFS(OutputAggregator.scala:187)
	at com.databricks.backend.daemon.driver.OutputAggregator$$anonfun$3.apply(OutputAggregator.scala:147)
	at com.databricks.backend.daemon.driver.OutputAggregator$$anonfun$3.apply(OutputAggregator.scala:146)
	at scala.Option.map(Option.scala:146)
	at com.databricks.backend.daemon.driver.OutputAgg

In [26]:
def array_to_string(my_list):
    return '[' + ','.join([str(elem) for elem in my_list]) + ']'

array_to_string_udf = udf(array_to_string,StringType())

agg_output_df2 = agg_output_df.withColumn('unigram_list_str',array_to_string_udf(F.col("unigram_list"))).withColumn('bigram_list_str',array_to_string_udf(F.col("bigram_list"))).drop("unigram_list").drop("bigram_list")

In [27]:
display(agg_output_df2)

zipcode unigram_list_str bigram_list_str 78736 [[Barbara, great, host, stayed, three, months, summer, Austin, thoroughly, enjoyed, time, knowledge, area, give, useful, tips, visit, get, around, enjoy, hiking, able, give, several, beautiful, locations, visit, Austin, One, time, even, went, hiking, together, small, group, Canyonlands, Trails, great, experience, location, calm, peaceful, tree, outside, bedroom, window, covered, blossoms, one, point, making, picturesque, view, pool, took, dip, pool, several, time, hot, summer, especially, refreshing, nice, way, relax, couple, hours, living, room, kitchen, shared, space, nice, hang, evenings, eating, dinner, watching, episodes, Office, fans, show, )., plan, staying, long, term, daily, commute, want, check, traffic, conditions, since, certain, parts, Austin, prone, heavy, traffic, personally, worth, driving, little, longer, great, summer, staying, Barbara],[Absolutely, wonderful, Bab, amazing, hostess, adorable, feline, allergic, cats, worries, Bab, let, room, you're, Miss, Kitty, loveable, room, perfect, complete, work, desk, home, spotless, ever, let, room, go, highly, recommend, book, one, asap, :)],[Oh, Babs, miss, Miss, Kitty, already, !!, Okay, everyone, hostess, mostess, Absolutely, lovely, every, way, adorable, kitty, Beautiful, room, sanctuary, perfect, remote, workers, Book, come, back, lol],[Babs, excellent, host, reasonable, expectations, tenants, always, willing, communicate, Highly, recommend],[first, time, using, Airbnb, services, experience, good, Mrs, Kelly, responsible, diligence, contacting, us, recommend, barn],[barn, unique, industrial, charm, lots, open, space, stayed, 2, nights, baby, loved, crawling, around, watching, chickens, yard, host, sweet, hospitable, left, toys, snacks, personal, touch, Would, stay, definitely, recommend, anyone, looking, peaceful, quiet, spot],[place, amazing, It's, perfect, type, stay, Austin, enjoyed, everything, hosts, hospitality, unrivaled, highly, recommend, staying, area, want, cozy, well, equipped, space, stay],[second, time, staying, Barn, feels, like, home, home, us, Improvements, made, since, last, stay, mad, even, better, Kelly's, communication, great, start, finish, lovely, homely, touches, added, great, experience, It's, bit, side, town, bonus, us, away, hustle, bustle],[many, ways, Barn, better, advertised, really, awesome, space, group, loved, staying, hosts, helpful, really, nice, people, Kelly, great, eye, decorating, really, shows, Can't, stress, enough, much, loved, space, said, there's, things, wish, aware, booked, First, distance, Barn, 11, miles, outside, city, limits, Depending, time, day, could, get, Austin, 25/30, mins, kind, freaked, first, went, check, took, us, hour, get, 4pm, check, downtown, Austin, rush, hour, brutal, I'd, highly, recommend, requesting, early, late, check-in, Distance, isn't, big, deal, whole, group, staying, together, Barn, group, 13, five, stayed, Barn, 10, stayed, downtown, hotel, barn, little, bit, far, downtown, guys, come, use, planned, BBQ, hang, etc, )., 2nd, barn, advertises, sleep, 5-9, people, plenty, room, 3, 5, beds, real, mattresses, two, air, mattresses, )., still, high, quality, minor, grumblings, guys, got, later, take, air, mattresses, There's, one, bathroom, nicely, done, fine, group, 5, guys, 3rd, barn, advertises, place, host, events, yet, pretty, excessive, ", guest, fee, .", Host, charged, us, $10/head, friends, hours, thought, unusual, AirBnB, deterred, us, using, Barn, much, probably, would, group, loved, Barn, wish, little, closer, town],[Barn, clean, exactly, advertised, Would, recommend, anyone, looking, visit, Austin],[could, made, better, choice, booking, barn, group, 8, girls, pictures, true, find, barn, reality, exceeded, expectations, spacious, yet, cozy, nicely, Texas, themed, decorated, enjoyed, everyone’s, first, impression, walked, felt, welcomed, especially, noticed, Kelly’s, hospitable, gestures, clean, ambiance, homey, well, organized, bit, worri